In [19]:
import sys

!{sys.executable} -W ignore:DEPRECATION -m pip install --quiet duckdb==0.7.1 \
duckdb-engine \
watermark \
jupysql \
sqlalchemy \
python-snappy \
pyarrow \
memray \
pandas \
ipywidgets  \
matplotlib \
gensim \
nltk \
plotly \
redis==4.5.3 \
jupyter-black \
sentence-transformers==2.2.1

In [70]:
# set log level for model training
import logging

logger = logging.getLogger()
logger.setLevel(logging.INFO)
logging.basicConfig(
    format="%(levelname)s - %(asctime)s: %(message)s",
    datefmt="%H:%M:%S",
    level=logging.INFO,
)

In [92]:
import pandas as pd

# Import embedding data
pqt = pd.read_parquet("/Users/vicki/viberary/viberary/src/data/learned_embeddings.snappy")

embedding_dict = dict(zip(pqt["index"], pqt["embeddings"]))


In [114]:
import pandas as pd

# Import embedding data
pqt = pd.read_parquet("/Users/vicki/viberary/viberary/src/data/learned_embeddings.snappy")
title_dict = dict(zip(pqt["index"], pqt["sentence"]))

In [81]:
# set up redis index
from redis import Redis
from redis.commands.search.field import VectorField, TextField
from redis.commands.search.query import Query

# Examples https://github.com/RediSearch/RediSearch/blob/master/docs/docs/vecsim-hybrid_queries_examples.ipynb
# More: https://lablab.ai/t/efficient-vector-similarity-search-with-redis-a-step-by-step-tutorial

# Redis client connection
host = "localhost"
port = 6379

redis_conn = Redis(host=host, port=port)

In [ ]:
 for i, (k, v) in enumerate(title_dict.items()):
            try:
                # write to Redis
                redis_conn.set(f"title::{k}", v)
                logging.info(f"Set {i} title into Redis")
            except Exception as e:
                logging.error("An exception occurred: {}".format(e))

In [104]:
# Index fields and configurations
# Params  https://redis.io/docs/stack/search/reference/vectors/

n_vec = 158872
dim = 384
M = 50  # Optional Number of maximum allowed outgoing edges for each node in the graph in each layer.
EF = 200  # Number of maximum allowed potential outgoing edges candidates for each node in the graph
vector_field = "vector"
token_field_name = "token"
index_name = "viberary"
distance_metric = "COSINE"
float_type = "FLOAT64"

In [108]:
import itertools 

def delete_data(client: Redis):
    client.flushall()

# Vectors in redis are stored in a binary blob
def load_docs(client: Redis, n, d, vector_dict):
    for i, (k, v) in enumerate(vector_dict.items()):
        logging.info(f"Inserting {i} vector into Redis index {index_name}")
        np_vector = v.astype(np.float64)
        try:
            # try storing vector, log exceptions if fails to map
            client.hset(k, mapping={vector_field: np_vector.tobytes()})
        except Exception as e:
            logging.error("An exception occurred: {}".format(e))


def print_results(res):
    docs = [int(doc.id) for doc in res.docs]
    dists = [float(doc.dist) if hasattr(doc, "dist") else "-" for doc in res.docs]
    print(f"got {len(docs)} doc ids: ", docs)
    print("\ndistances: ", dists)

In [109]:
# Delete and rebuild index
delete_data(redis_conn)

schema = (
    VectorField(
        vector_field,
        "FLAT",
        {"TYPE": float_type, 
         "DIM": dim, 
         "DISTANCE_METRIC": distance_metric},
    ),
    TextField(token_field_name),
)

redis_conn.ft(index_name).create_index(schema)
redis_conn.ft(index_name).config_set("default_dialect", 2)
load_docs(redis_conn, n_vec, dim, embedding_dict)

INFO - 15:18:14: Inserting 0 vector into Redis index viberary
INFO - 15:18:14: Inserting 1 vector into Redis index viberary
INFO - 15:18:14: Inserting 2 vector into Redis index viberary
INFO - 15:18:14: Inserting 3 vector into Redis index viberary
INFO - 15:18:14: Inserting 4 vector into Redis index viberary
INFO - 15:18:14: Inserting 5 vector into Redis index viberary
INFO - 15:18:14: Inserting 6 vector into Redis index viberary
INFO - 15:18:14: Inserting 7 vector into Redis index viberary
INFO - 15:18:14: Inserting 8 vector into Redis index viberary
INFO - 15:18:14: Inserting 9 vector into Redis index viberary
INFO - 15:18:14: Inserting 10 vector into Redis index viberary
INFO - 15:18:14: Inserting 11 vector into Redis index viberary
INFO - 15:18:14: Inserting 12 vector into Redis index viberary
INFO - 15:18:14: Inserting 13 vector into Redis index viberary
INFO - 15:18:14: Inserting 14 vector into Redis index viberary
INFO - 15:18:14: Inserting 15 vector into Redis index viberary
IN

INFO - 15:18:14: Inserting 130 vector into Redis index viberary
INFO - 15:18:14: Inserting 131 vector into Redis index viberary
INFO - 15:18:14: Inserting 132 vector into Redis index viberary
INFO - 15:18:14: Inserting 133 vector into Redis index viberary
INFO - 15:18:14: Inserting 134 vector into Redis index viberary
INFO - 15:18:14: Inserting 135 vector into Redis index viberary
INFO - 15:18:14: Inserting 136 vector into Redis index viberary
INFO - 15:18:14: Inserting 137 vector into Redis index viberary
INFO - 15:18:14: Inserting 138 vector into Redis index viberary
INFO - 15:18:14: Inserting 139 vector into Redis index viberary
INFO - 15:18:14: Inserting 140 vector into Redis index viberary
INFO - 15:18:14: Inserting 141 vector into Redis index viberary
INFO - 15:18:14: Inserting 142 vector into Redis index viberary
INFO - 15:18:14: Inserting 143 vector into Redis index viberary
INFO - 15:18:14: Inserting 144 vector into Redis index viberary
INFO - 15:18:14: Inserting 145 vector in

INFO - 15:18:14: Inserting 259 vector into Redis index viberary
INFO - 15:18:14: Inserting 260 vector into Redis index viberary
INFO - 15:18:14: Inserting 261 vector into Redis index viberary
INFO - 15:18:14: Inserting 262 vector into Redis index viberary
INFO - 15:18:14: Inserting 263 vector into Redis index viberary
INFO - 15:18:14: Inserting 264 vector into Redis index viberary
INFO - 15:18:14: Inserting 265 vector into Redis index viberary
INFO - 15:18:14: Inserting 266 vector into Redis index viberary
INFO - 15:18:14: Inserting 267 vector into Redis index viberary
INFO - 15:18:14: Inserting 268 vector into Redis index viberary
INFO - 15:18:14: Inserting 269 vector into Redis index viberary
INFO - 15:18:14: Inserting 270 vector into Redis index viberary
INFO - 15:18:14: Inserting 271 vector into Redis index viberary
INFO - 15:18:14: Inserting 272 vector into Redis index viberary
INFO - 15:18:14: Inserting 273 vector into Redis index viberary
INFO - 15:18:14: Inserting 274 vector in

INFO - 15:18:15: Inserting 388 vector into Redis index viberary
INFO - 15:18:15: Inserting 389 vector into Redis index viberary
INFO - 15:18:15: Inserting 390 vector into Redis index viberary
INFO - 15:18:15: Inserting 391 vector into Redis index viberary
INFO - 15:18:15: Inserting 392 vector into Redis index viberary
INFO - 15:18:15: Inserting 393 vector into Redis index viberary
INFO - 15:18:15: Inserting 394 vector into Redis index viberary
INFO - 15:18:15: Inserting 395 vector into Redis index viberary
INFO - 15:18:15: Inserting 396 vector into Redis index viberary
INFO - 15:18:15: Inserting 397 vector into Redis index viberary
INFO - 15:18:15: Inserting 398 vector into Redis index viberary
INFO - 15:18:15: Inserting 399 vector into Redis index viberary
INFO - 15:18:15: Inserting 400 vector into Redis index viberary
INFO - 15:18:15: Inserting 401 vector into Redis index viberary
INFO - 15:18:15: Inserting 402 vector into Redis index viberary
INFO - 15:18:15: Inserting 403 vector in

INFO - 15:18:15: Inserting 517 vector into Redis index viberary
INFO - 15:18:15: Inserting 518 vector into Redis index viberary
INFO - 15:18:15: Inserting 519 vector into Redis index viberary
INFO - 15:18:15: Inserting 520 vector into Redis index viberary
INFO - 15:18:15: Inserting 521 vector into Redis index viberary
INFO - 15:18:15: Inserting 522 vector into Redis index viberary
INFO - 15:18:15: Inserting 523 vector into Redis index viberary
INFO - 15:18:15: Inserting 524 vector into Redis index viberary
INFO - 15:18:15: Inserting 525 vector into Redis index viberary
INFO - 15:18:15: Inserting 526 vector into Redis index viberary
INFO - 15:18:15: Inserting 527 vector into Redis index viberary
INFO - 15:18:15: Inserting 528 vector into Redis index viberary
INFO - 15:18:15: Inserting 529 vector into Redis index viberary
INFO - 15:18:15: Inserting 530 vector into Redis index viberary
INFO - 15:18:15: Inserting 531 vector into Redis index viberary
INFO - 15:18:15: Inserting 532 vector in

...

INFO - 15:20:32: Inserting 84423 vector into Redis index viberary
INFO - 15:20:32: Inserting 84424 vector into Redis index viberary
INFO - 15:20:32: Inserting 84425 vector into Redis index viberary
INFO - 15:20:32: Inserting 84426 vector into Redis index viberary
INFO - 15:20:32: Inserting 84427 vector into Redis index viberary
INFO - 15:20:32: Inserting 84428 vector into Redis index viberary
INFO - 15:20:32: Inserting 84429 vector into Redis index viberary
INFO - 15:20:32: Inserting 84430 vector into Redis index viberary
INFO - 15:20:32: Inserting 84431 vector into Redis index viberary
INFO - 15:20:32: Inserting 84432 vector into Redis index viberary
INFO - 15:20:32: Inserting 84433 vector into Redis index viberary
INFO - 15:20:32: Inserting 84434 vector into Redis index viberary
INFO - 15:20:32: Inserting 84435 vector into Redis index viberary
INFO - 15:20:32: Inserting 84436 vector into Redis index viberary
INFO - 15:20:32: Inserting 84437 vector into Redis index viberary
INFO - 15:

INFO - 15:20:32: Inserting 84548 vector into Redis index viberary
INFO - 15:20:32: Inserting 84549 vector into Redis index viberary
INFO - 15:20:32: Inserting 84550 vector into Redis index viberary
INFO - 15:20:32: Inserting 84551 vector into Redis index viberary
INFO - 15:20:32: Inserting 84552 vector into Redis index viberary
INFO - 15:20:32: Inserting 84553 vector into Redis index viberary
INFO - 15:20:32: Inserting 84554 vector into Redis index viberary
INFO - 15:20:32: Inserting 84555 vector into Redis index viberary
INFO - 15:20:32: Inserting 84556 vector into Redis index viberary
INFO - 15:20:32: Inserting 84557 vector into Redis index viberary
INFO - 15:20:32: Inserting 84558 vector into Redis index viberary
INFO - 15:20:32: Inserting 84559 vector into Redis index viberary
INFO - 15:20:32: Inserting 84560 vector into Redis index viberary
INFO - 15:20:32: Inserting 84561 vector into Redis index viberary
INFO - 15:20:32: Inserting 84562 vector into Redis index viberary
INFO - 15:

INFO - 15:20:32: Inserting 84673 vector into Redis index viberary
INFO - 15:20:32: Inserting 84674 vector into Redis index viberary
INFO - 15:20:32: Inserting 84675 vector into Redis index viberary
INFO - 15:20:32: Inserting 84676 vector into Redis index viberary
INFO - 15:20:32: Inserting 84677 vector into Redis index viberary
INFO - 15:20:32: Inserting 84678 vector into Redis index viberary
INFO - 15:20:32: Inserting 84679 vector into Redis index viberary
INFO - 15:20:32: Inserting 84680 vector into Redis index viberary
INFO - 15:20:32: Inserting 84681 vector into Redis index viberary
INFO - 15:20:32: Inserting 84682 vector into Redis index viberary
INFO - 15:20:32: Inserting 84683 vector into Redis index viberary
INFO - 15:20:32: Inserting 84684 vector into Redis index viberary
INFO - 15:20:32: Inserting 84685 vector into Redis index viberary
INFO - 15:20:32: Inserting 84686 vector into Redis index viberary
INFO - 15:20:32: Inserting 84687 vector into Redis index viberary
INFO - 15:

INFO - 15:20:33: Inserting 84798 vector into Redis index viberary
INFO - 15:20:33: Inserting 84799 vector into Redis index viberary
INFO - 15:20:33: Inserting 84800 vector into Redis index viberary
INFO - 15:20:33: Inserting 84801 vector into Redis index viberary
INFO - 15:20:33: Inserting 84802 vector into Redis index viberary
INFO - 15:20:33: Inserting 84803 vector into Redis index viberary
INFO - 15:20:33: Inserting 84804 vector into Redis index viberary
INFO - 15:20:33: Inserting 84805 vector into Redis index viberary
INFO - 15:20:33: Inserting 84806 vector into Redis index viberary
INFO - 15:20:33: Inserting 84807 vector into Redis index viberary
INFO - 15:20:33: Inserting 84808 vector into Redis index viberary
INFO - 15:20:33: Inserting 84809 vector into Redis index viberary
INFO - 15:20:33: Inserting 84810 vector into Redis index viberary
INFO - 15:20:33: Inserting 84811 vector into Redis index viberary
INFO - 15:20:33: Inserting 84812 vector into Redis index viberary
INFO - 15:

INFO - 15:20:33: Inserting 84923 vector into Redis index viberary
INFO - 15:20:33: Inserting 84924 vector into Redis index viberary
INFO - 15:20:33: Inserting 84925 vector into Redis index viberary
INFO - 15:20:33: Inserting 84926 vector into Redis index viberary
INFO - 15:20:33: Inserting 84927 vector into Redis index viberary
INFO - 15:20:33: Inserting 84928 vector into Redis index viberary
INFO - 15:20:33: Inserting 84929 vector into Redis index viberary
INFO - 15:20:33: Inserting 84930 vector into Redis index viberary
INFO - 15:20:33: Inserting 84931 vector into Redis index viberary
INFO - 15:20:33: Inserting 84932 vector into Redis index viberary
INFO - 15:20:33: Inserting 84933 vector into Redis index viberary
INFO - 15:20:33: Inserting 84934 vector into Redis index viberary
INFO - 15:20:33: Inserting 84935 vector into Redis index viberary
INFO - 15:20:33: Inserting 84936 vector into Redis index viberary
INFO - 15:20:33: Inserting 84937 vector into Redis index viberary
INFO - 15:

In [110]:
# Check to make sure we indexed shit
print("index size: ", redis_conn.ft("viberary").info()["num_docs"])

index size:  84945


In [111]:
from sentence_transformers import SentenceTransformer
model = SentenceTransformer('all-MiniLM-L6-v2')

#Our sentences we like to encode
sentences = ['happy book']

embedding = model.encode(sentences)

INFO - 15:21:32: Load pretrained SentenceTransformer: all-MiniLM-L6-v2
INFO - 15:21:32: Use pytorch device: cpu


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

In [112]:
import pprint
import numpy as np


query_vector = embedding.astype(np.float64).tobytes()
topK = 10
q = (
    Query(f"*=>[KNN {topK} @{vector_field} $vec_param AS vector_score]")
    .sort_by("vector_score")
    .paging(0, topK)
    .return_fields("token", "vector_score")
    .dialect(2)
)
params_dict = {"vec_param": query_vector}

# Return results
results = redis_conn.ft("viberary").search(q, query_params=params_dict)
results_docs = results.docs

pp = pprint.PrettyPrinter(indent=4)
pp.pprint(results.docs)

[   Document {'id': '11832', 'payload': None, 'vector_score': '0.354756735837'},
    Document {'id': '81286', 'payload': None, 'vector_score': '0.367813969639'},
    Document {'id': '44295', 'payload': None, 'vector_score': '0.375284464942'},
    Document {'id': '46275', 'payload': None, 'vector_score': '0.385229077495'},
    Document {'id': '64889', 'payload': None, 'vector_score': '0.403392342117'},
    Document {'id': '6128', 'payload': None, 'vector_score': '0.406003857825'},
    Document {'id': '42131', 'payload': None, 'vector_score': '0.416364511754'},
    Document {'id': '69728', 'payload': None, 'vector_score': '0.417359490564'},
    Document {'id': '80700', 'payload': None, 'vector_score': '0.423923562341'},
    Document {'id': '19969', 'payload': None, 'vector_score': '0.430933296825'}]


In [113]:
index_vector = []

for i in results_docs:
    id = i["id"]  # bookid
    id_int = id.lstrip("vector::")
    title = redis_conn.get(f"title::{id_int}")
    index_vector.append((i["id"], i["vector_score"], title.decode()))

AttributeError: 'NoneType' object has no attribute 'decode'

In [77]:
index_vector

[]